In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import folium
import numpy as np
from folium import plugins

In [4]:
from rlway.pyosrd import OSRD

In [5]:
# france = OSRD('../data', infra_json='France avec BP_CC.id24.railjson.json')
france = OSRD('../data', infra_json='France.id3.railjson.3.4.9.json')

In [6]:
# france.infra = france.infra['data']

In [7]:
line_names = [
    (t['extensions']['sncf']['line_name']) 
    for t in france.infra['track_sections']
]
line_codes = [
    (t['extensions']['sncf']['line_code']) 
    for t in france.infra['track_sections']
]

In [8]:
import pandas as pd

lignes = pd.DataFrame({
    'name': line_names,
    'code': line_codes
}).drop_duplicates().reset_index(drop=True)

In [9]:
lignes[lignes['name'].str.contains('saintes', case=False)]

name    code
189  Ligne de Nantes-Orléans à Saintes  530000
293           Ligne de Saintes à Royan  544000

In [10]:
from typing import Dict, Any, Union, List

def filter_by_track_section_ids(
    infra: Dict[str, Any],
    track_section_ids: List[str]
)-> Dict[str, Any]:

    subinfra = infra.copy()

    # 'version'
    # subinfra["version"] = infra['version']
    
    # 'track_sections'

    subinfra['track_sections'] = [
        track for track in infra['track_sections'] if track['id']in track_section_ids
    ]

    # 'signals'
    subinfra['signals'] = [
        signal for signal in infra['signals'] if signal['track'] in track_section_ids
    ]

    # 'speed_sections'


    # 'detectors'
    subinfra['detectors'] = [
        detector for detector in infra['detectors'] if detector['track'] in track_section_ids
    ]
    detector_ids = [detector['id'] for detector in subinfra['detectors']]

    # 'track_section_links'
    # subinfra['track_section_links'] = [
    #     link for link in infra['track_section_links']
    #     if link['src']['track'] in track_section_ids or link['src']['track'] in track_section_ids
    # ]

    # 'switches'
    # subinfra['switches'] = infra['switches']

    switch_ids = set()
    for switch in infra['switches']:
        for track in [switch['ports'][port]['track'] for port in switch['ports']]:
            if track in track_section_ids:
                switch_ids.add(switch['id'])

    subinfra['switches'] = [
        switch
        for switch in infra['switches']
        if switch['id'] in switch_ids
    ]

    for switch in subinfra['switches']:
        switch['ports'] = {
            port: details
            for port, details in switch['ports'].items()
            if details['track'] in track_section_ids
        }

    # 'switch_types'
    # subinfra['switch_types'] = infra['switch_types']

    # 'buffer_stops'
    subinfra['buffer_stops'] = [
        buffer_stop
        for buffer_stop in infra['buffer_stops']
        if buffer_stop['track'] in track_section_ids
    ]

    # 'routes'
    # subinfra['routes'] = infra['routes']

    # 'operational_points'
    op_ids = set()
    for op in infra['operational_points']:
        for track in [part['track'] for part in op['parts']]:
            if track in track_section_ids:
                op_ids.add(op['id'])

    subinfra['operational_points'] = [
        op
        for op in infra['operational_points']
        if op['id'] in op_ids
    ]

    for op in subinfra['operational_points']:
        op['parts'] = [part for part in op['parts'] if part['track'] in track_section_ids]

    # 'catenaries'


    # 'dead_sections'

    return subinfra

def filter_by_line_codes(infra: Dict[str, Any], codes: Union[int, List[int]]) -> Dict[str, Any]:

    if not isinstance(codes, list):
        codes = [codes]

    track_section_ids = [
        track['id'] for track in infra['track_sections'] if track['extensions']['sncf']['line_code'] in codes
    ]

    return filter_by_track_section_ids(infra, track_section_ids)
    

In [11]:
# infra = filter_by_line_codes(france.infra, [570000, 570390, 610000, 579000])
infra = filter_by_line_codes(france.infra, [880000, ])


In [12]:
# from rlway.pyosrd.viz.map import folium_map

line = OSRD('./tmp')
line.infra = infra

In [13]:
op_pts = pd.json_normalize(france.infra['operational_points'])
op_pts['nb_tracks'] = op_pts['parts'].apply(lambda x: len(x))
op_pts.loc[
    # op_pts['extensions.identifier.name'].str.contains('Austerlitz')
    # &
    op_pts['extensions.sncf.ch_long_label'].str.contains('Bâtiment Voyageurs')
][['extensions.sncf.ch_long_label', 'extensions.identifier.name', 'nb_tracks','id']]

extensions.sncf.ch_long_label extensions.identifier.name  nb_tracks  \
6               Bâtiment Voyageurs            Bourg-St-Andéol          3   
16              Bâtiment Voyageurs                Vic-Bigorre          1   
28              Bâtiment Voyageurs        Marseille-Blancarde          9   
38              Bâtiment Voyageurs          Sathonay-Rillieux          4   
45              Bâtiment Voyageurs   Villefranche-du-Périgord          1   
...                            ...                        ...        ...   
9004            Bâtiment Voyageurs                  Montereau          6   
9012            Bâtiment Voyageurs              Longeray-Léaz          5   
9015            Bâtiment Voyageurs                      Ussel          2   
9016            Bâtiment Voyageurs            Cambo-les-Bains          2   
9017            Bâtiment Voyageurs                 Obermodern          4   

                                        id  
6     d9e4c97a-6667-11e3-89ff-01f464e0362d  
16    d97e7b88-6667-11e3-89ff-01f464e0362d  
28    d94ada10-6667-11e3-89ff-01f464e0362d  
38    d9e1f1e2-6667-11e3-89ff-01f464e0362d  
45    d948f7ce-6667-11e3-89ff-01f464e0362d  
...                                    ...  
9004  d9d31300-6667-11e3-89ff-01f464e0362d  
9012  d9a60622-6667-11e3-89ff-01f464e0362d  
9015  d983177c-6667-11e3-89ff-01f464e0362d  
9016  d9c8a5f8-6667-11e3-89ff-01f464e0362d  
9017  d9ccd2ee-6667-11e3-89ff-01f464e0362d  

[1330 rows x 4 columns]

In [14]:
pd.json_normalize(line.infra['operational_points']).columns

Index(['id', 'parts', 'extensions.sncf.ch', 'extensions.sncf.ci',
       'extensions.sncf.trigram', 'extensions.sncf.ch_long_label',
       'extensions.sncf.ch_short_label', 'extensions.identifier.uic',
       'extensions.identifier.name'],
      dtype='object')

In [15]:
track_sections = pd.json_normalize(france.infra['track_sections'])
op = pd.json_normalize(france.infra['operational_points'])


In [16]:
op

id  \
0     d99368f6-6667-11e3-89ff-01f464e0362d   
1     d9e9c544-6667-11e3-89ff-01f464e0362d   
2     d9863d36-6667-11e3-89ff-01f464e0362d   
3     d9e0eb78-6667-11e3-89ff-01f464e0362d   
4     d97e4a32-6667-11e3-89ff-01f464e0362d   
...                                    ...   
9019  d97c8574-6667-11e3-89ff-01f464e0362d   
9020  d981924a-6667-11e3-89ff-01f464e0362d   
9021  d9baec1c-6667-11e3-89ff-01f464e0362d   
9022  d9c78234-6667-11e3-89ff-01f464e0362d   
9023  d9b75bae-6667-11e3-89ff-01f464e0362d   

                                                  parts extensions.sncf.ch  \
0     [{'track': '62f7a13c-6667-11e3-81ff-01f464e036...                 V4   
1     [{'track': '62e2bb52-6667-11e3-81ff-01f464e036...                 SG   
2     [{'track': '686af830-6667-11e3-81ff-01f464e036...                 00   
3     [{'track': '864cd63c-45c5-11e9-80ff-01d06fb51c...                 ES   
4     [{'track': '60b3cf0e-6667-11e3-81ff-01f464e036...                 VC   
...                                                 ...                ...   
9019  [{'track': '601ebe06-6667-11e3-81ff-01f464e036...                 00   
9020  [{'track': '61a1b9d6-6667-11e3-81ff-01f464e036...                 91   
9021  [{'track': '6b0ba5aa-6667-11e3-81ff-01f464e036...                 00   
9022  [{'track': '60527c80-6667-11e3-81ff-01f464e036...                 RF   
9023  [{'track': 'e3f48ac6-8117-11eb-aeff-0114b22731...                 00   

      extensions.sncf.ci extensions.sncf.trigram  \
0                 686675                     PGV   
1                 772400                     LCY   
2                 595702                     VSJ   
3                 611897                     CTN   
4                 765040                      AF   
...                  ...                     ...   
9019              181016                     XLX   
9020              396564                     ECO   
9021              193151                     TEC   
9022              394007                      CH   
9023              781245                     VBZ   

         extensions.sncf.ch_long_label extensions.sncf.ch_short_label  \
0         Voies 4 à 10 (Remisage Pair)                   Voies 4 à 10   
1     Poste de Sectionnement Genouilly                   PS Genouilly   
2                                   00                             00   
3                         ITE Km 189,2                   ITE Km 189,2   
4                    Aiguille Km 743,9                   Aig Km 743,9   
...                                ...                            ...   
9019                                00                             00   
9020                         Carré C91                      Carré C91   
9021                                00                             00   
9022                                RF                             RF   
9023                                00                             00   

      extensions.identifier.uic extensions.identifier.name  
0                      87686675       Paris-Bercy-Conflans  
1                      87772400  Poste 19 Lacour-d'Arcenay  
2                      87595702              Les Versannes  
3                      87611897             Castelsarrasin  
4                      87765040        Avignon-Champfleury  
...                         ...                        ...  
9019                   87181016       St-Louis-la-Chaussée  
9020                   87396564                    Écommoy  
9021                   87193151                  Téterchen  
9022                   87394007                   Chartres  
9023                   87781245     Villeneuve-lès-Béziers  

[9024 rows x 9 columns]

In [17]:
pd.json_normalize(op[op['extensions.identifier.name'].str.contains('Angoulême')].loc[171].parts).merge(
    track_sections[['id', 'extensions.sncf.track_name', 'extensions.sncf.line_code']], left_on='track', right_on='id'
)
# op[op['extensions.identifier.name'].str.contains('Poitiers')]

track  position extensions.sncf.kp  \
0  60948172-6667-11e3-81ff-01f464e0362d       374            449+384   
1  63a1a218-6667-11e3-81ff-01f464e0362d       514            449+384   
2  68b71990-6667-11e3-81ff-01f464e0362d       464            449+384   
3  609818aa-6667-11e3-81ff-01f464e0362d       554            449+384   
4  68fc1ede-6667-11e3-81ff-01f464e0362d       374            449+384   

                                     id extensions.sncf.track_name  \
0  60948172-6667-11e3-81ff-01f464e0362d                         V2   
1  63a1a218-6667-11e3-81ff-01f464e0362d                          6   
2  68b71990-6667-11e3-81ff-01f464e0362d                          Z   
3  609818aa-6667-11e3-81ff-01f464e0362d                         V1   
4  68fc1ede-6667-11e3-81ff-01f464e0362d                          4   

   extensions.sncf.line_code  
0                     570000  
1                     570000  
2                     570000  
3                     570000  
4                     570000

In [18]:
def platforms(
    self,
    station: str,
):
    track_sections = pd.json_normalize(self.infra['track_sections'])
    op = pd.json_normalize(self.infra['operational_points'])

    if station not in op['extensions.identifier.name'].unique():
        print(f'{station} is not a valid station in the infra. Did you mean any of these ?')
        print(
            op[
                op['extensions.identifier.name'].str.contains(station.lower(), case=False)
            ]['extensions.identifier.name'].unique()
        )

    op_station = op[
        op['extensions.identifier.name'] == station
    ]
    
    op_station_platforms = op_station[
        op_station['extensions.sncf.ch'].isin(['BV', '00'])
    ]

    if len(op_station_platforms) == 0:
        return {}
    
    df = (
        pd.json_normalize(op_station_platforms.iloc[0].parts)
        .merge(
            track_sections[['id', 'extensions.sncf.track_name', 'extensions.sncf.line_code']],
            left_on='track',
            right_on='id'
        )
    )

    return {
        row['extensions.sncf.track_name']: {'track_section': row['track'], 'offset': row['position'], 'line_code': row['extensions.sncf.line_code']}
        for i, row in df.iterrows()
    }

In [19]:
def platform_location(
    self,
    station: str,
    track_name: str,
):
    platform = platforms(self, station)[track_name]
    return (platform['track_section'], platform['offset'])

In [28]:
platforms(france, 'Bourg-en-Bresse')

{'V2': {'track_section': '61409dac-6667-11e3-81ff-01f464e0362d',
  'offset': 453,
  'line_code': 880000},
 'V1': {'track_section': '629948d6-6667-11e3-81ff-01f464e0362d',
  'offset': 396,
  'line_code': 880000}}

In [21]:
france.simulation

{'train_schedule_groups': [{'schedules': [{'id': 'TGV',
     'departure_time': 0,
     'initial_speed': 0.0,
     'rolling_stock': 'fast_rolling_stock',
     'stops': [{'duration': 1, 'position': -1}],
     'allowances': []}],
   'waypoints': [[{'track_section': '68b71990-6667-11e3-81ff-01f464e0362d',
      'offset': 464,
      'direction': 'START_TO_STOP'},
     {'track_section': '68b71990-6667-11e3-81ff-01f464e0362d',
      'offset': 464,
      'direction': 'STOP_TO_START'}],
    [{'track_section': '6169979e-6667-11e3-81ff-01f464e0362d',
      'offset': 336,
      'direction': 'START_TO_STOP'},
     {'track_section': '6169979e-6667-11e3-81ff-01f464e0362d',
      'offset': 336,
      'direction': 'STOP_TO_START'}]],
   'id': 'group.0'}],
 'rolling_stocks': [],
 'time_step': 2.0}

In [22]:
import os
from railjson_generator import SimulationBuilder

built_simulation = SimulationBuilder().build()
built_simulation.save(os.path.join(france.dir, france.simulation_json))

In [25]:
pd.json_normalize(france.infra['switches']).switch_type.value_counts()

switch_type
point_switch          13944
link                   9485
double_slip_switch     1693
crossing                113
Name: count, dtype: int64

In [38]:
sw = (s for s in france.infra['switches'])


In [1]:
next(sw)

NameError: name 'sw' is not defined

In [177]:
france.simulation = {
  "train_schedule_groups": [],
  "rolling_stocks": [],
  "time_step": 2.0
}

In [178]:
france.add_train(
    label='TGV',
    locations=[
        platform_location(france, 'Angoulême', 'Z'),
        platform_location(france, 'Bordeaux-St-Jean', '6')
    ],
    departure_time=0
)

In [180]:
france.simulation

{'train_schedule_groups': [{'schedules': [{'id': 'TGV',
     'departure_time': 0,
     'initial_speed': 0.0,
     'rolling_stock': 'fast_rolling_stock',
     'stops': [{'duration': 1, 'position': -1}],
     'allowances': []}],
   'waypoints': [[{'track_section': '68b71990-6667-11e3-81ff-01f464e0362d',
      'offset': 464,
      'direction': 'START_TO_STOP'},
     {'track_section': '68b71990-6667-11e3-81ff-01f464e0362d',
      'offset': 464,
      'direction': 'STOP_TO_START'}],
    [{'track_section': '6169979e-6667-11e3-81ff-01f464e0362d',
      'offset': 336,
      'direction': 'START_TO_STOP'},
     {'track_section': '6169979e-6667-11e3-81ff-01f464e0362d',
      'offset': 336,
      'direction': 'STOP_TO_START'}]],
   'id': 'group.0'}],
 'rolling_stocks': [],
 'time_step': 2.0}

In [183]:
france.run()

[15:03:18,052] [INFO]  [StandaloneSimulationCommand] Loading infra: ../data/France.id3.railjson.3.4.9.json
[15:03:19,215] [INFO]              [FullInfra] parsing infra


RuntimeError: Exception in thread "main" java.lang.NullPointerException: Cannot invoke "java.util.List.iterator()" because "infra.switchTypes" is null
	at fr.sncf.osrd.infra.implementation.tracks.undirected.UndirectedInfraBuilder.parse(UndirectedInfraBuilder.java:132)
	at fr.sncf.osrd.infra.implementation.tracks.undirected.UndirectedInfraBuilder.parseInfra(UndirectedInfraBuilder.java:117)
	at fr.sncf.osrd.infra.implementation.tracks.directed.DirectedInfraBuilder.fromRJS(DirectedInfraBuilder.java:54)
	at fr.sncf.osrd.infra.implementation.reservation.ReservationInfraBuilder.fromRJS(ReservationInfraBuilder.java:82)
	at fr.sncf.osrd.infra.implementation.signaling.SignalingInfraBuilder.fromRJSInfra(SignalingInfraBuilder.java:60)
	at fr.sncf.osrd.api.FullInfra.fromRJSInfra(FullInfra.java:31)
	at fr.sncf.osrd.cli.StandaloneSimulationCommand.loadInfra(StandaloneSimulationCommand.java:126)
	at fr.sncf.osrd.cli.StandaloneSimulationCommand.run(StandaloneSimulationCommand.java:71)
	at fr.sncf.osrd

In [154]:
line.folium_map()

- restreindre l'infra à une ou plusieurs lignes entre 2 gares ?
- créer des locations en début et fins de quais
- Points de départ et d'arrivée: Gare, voie et direction
  - ou alors gare et voie et la direction dépend de départ/destination ?
- Extraire des rolling stocks de la BDD ?

In [132]:
# folium_map(line)
line.folium_map()

In [ ]:
import networkx as nx

track_line_code = {
    track['id']: track['extensions']['sncf']['line_code']
    for track in france.infra['track_sections']
}
track_name = {
    track['id']: track['extensions']['sncf']['track_name']
    for track in france.infra['track_sections']
}

lignes[lignes.code==142000]['name'].item()

point = france._track_section_network


path = nx.shortest_path(point, '68e5091c-6667-11e3-81ff-01f464e0362d', '6097d366-6667-11e3-81ff-01f464e0362d',)

for point in path:
    print(track_name[point], track_line_code[point], lignes[lignes.code==track_line_code[point]]['name'].item())

Voie de jonction Brt 311A - Brt 311B de  Étampes 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie 1bis 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie 1bis 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie de jonction Brt 203A - Brt 203B de  Étampes 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie 1 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie 1 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie 1 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie 1 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie 1 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie de jonction TJD 315-316/317-318 - TJS 327/329 de Brétigny 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie 2 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie de jonction Brt 122 - Brt 123 de  Brétigny 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie 1 570000 Ligne de Paris-Austerlitz à Bordeaux-St-Jean
Voie 1 570000 Ligne de Paris-Austerlitz à Bord

In [ ]:
test = OSRD('./tmp')
test.infra = filter_by_track_section_ids(france.infra, path[1:])
test.folium_map()
